
# Solve a 2D short cantilever topology optimization problem


In [ ]:
from __future__ import annotations

from gemseo import configure_logger
from gemseo import create_scenario
from gemseo.problems.topo_opt.topopt_initialize import (
    initialize_design_space_and_discipline_to,
)

configure_logger()

## Setup the topology optimization problem
Define the target volume fraction:



In [ ]:
volume_fraction = 0.3

Define the problem type:



In [ ]:
problem_name = "Short_Cantilever"

Define the number of elements in the x- and y- directions:



In [ ]:
n_x = 50
n_y = 25

Define the full material Young's modulus and Poisson's ratio:



In [ ]:
e0 = 1
nu = 0.3

Define the penalty of the SIMP approach:



In [ ]:
penalty = 3

Define the minimum member size in the solution:



In [ ]:
min_memeber_size = 1.5

Instantiate the :class:`.DesignSpace` and the disciplines:



In [ ]:
design_space, disciplines = initialize_design_space_and_discipline_to(
    problem=problem_name,
    n_x=n_x,
    n_y=n_y,
    e0=e0,
    nu=nu,
    penalty=penalty,
    min_member_size=min_memeber_size,
    vf0=volume_fraction,
)

## Solve the topology optimization problem
Generate a :class:`.MDOScenario`:



In [ ]:
scenario = create_scenario(
    disciplines,
    formulation="DisciplinaryOpt",
    objective_name="compliance",
    design_space=design_space,
)

Add the volume fraction constraint to the scenario:



In [ ]:
scenario.add_constraint("volume fraction", "ineq", value=volume_fraction)

Generate the XDSM:



In [ ]:
scenario.xdsmize()

Execute the scenario:



In [ ]:
scenario.execute(input_data={"max_iter": 200, "algo": "NLOPT_MMA"})

## Results
Post-process the optimization history:



In [ ]:
scenario.post_process(
    "BasicHistory",
    variable_names=["compliance"],
    file_name=f"{problem_name}_history.png",
)

Plot the solution:



In [ ]:
scenario.post_process(
    "TopologyView",
    n_x=n_x,
    n_y=n_y,
    file_name=f"{problem_name}_solution.png",
)